# Program `GEMTB`
## Programmed by Tokuro Fukui

In [ ]:
#--------
# Module
#--------
import numpy as np
import mpmath as mp
import scipy as sp
from scipy.linalg import eigh
import matplotlib.pyplot as plt

# Tips 1 for exercise
- 重陽子を湯川型ポテンシャルで解こう
- 直下のセルにある湯川型ポテンシャルのパラメータを自分でサーチしてみよう
    - `gsq`: ポテンシャルの深さ
    - 現時点で`gsq`には適当な値が代入されている

In [ ]:
#-----------------
# Input variables
#-----------------
## Physical constants
pi = np.pi
hc = 197.3269601               # \hbar c (MeV fm)
m_p = 938.2720                 # Proton mass (MeV)
m_n = 939.5654                 # Neutron mass (MeV)
muac = m_p * m_n / (m_p + m_n) # Reduce mass (MeV)
m_pi = 138.04 / hc             # Pion mass (fm^{-1})
l = 0                          # Orbital angular momentum
gsq = 20.0                     # Interaction strength (MeV fm)

## GEM parameters
nbmx = 20  # Number of Gaussian basis functions
bmn = 0.5  # Minimum value of Gaussian range (fm)
bmx = 20.0 # Maximum value of Gaussian range (fm)
rho = (bmx / bmn)**(1 / (nbmx - 1))

## Wave-function output
rmx = 20.0 # Maximum value of output (fm)
dr = 0.1   # Increments of output (fm)
irmx = int(rmx / dr) + 1

## Wave-function output (momentum space)
kmx = 5.0 # Maximum value of output (fm^{-1})
dk = 0.02 # Increments of output (fm^{-1})
ikmx = int(kmx / dk) + 1

In [ ]:
#-----------------
# Matrix elements
#-----------------
## Arrays
nu = np.zeros(nbmx)           # Range parameter
Nfac = np.zeros(nbmx)         # Normalization factor
Nij = np.zeros((nbmx, nbmx))  # Norm-matrix elements
Hij = np.zeros((nbmx, nbmx))  # Hamiltonian-matrix elements

## Range parameter and normalization factor
for i in range(nbmx):
    # b = bmn * rho**(i - 1)
    b = bmn * rho**i
    nu[i] = 1.0 / b**2
    Nfac[i] = np.sqrt(2.0**(l + 2) / mp.fac2(2 * l + 1)) * ((2.0 * nu[i])**(2 * l + 3) / pi)**(0.25)

## Calculation of matrix elements
for i in range(nbmx):
    for j in range(i + 1):
        beta = 2.0 * np.sqrt(nu[i] * nu[j]) / (nu[i] + nu[j])
        Nij[i, j] = beta**(l + 1.5)
        Nij[j, i] = Nij[i, j]

        coeff_T = hc**2 / muac * (2.0 * l + 3.0) * nu[i] * nu[j] / (nu[i] + nu[j])
        Tij = coeff_T * Nij[i, j]

        nuij = nu[i] + nu[j]
        gamma = m_pi / (2.0 * nuij)
        I0 = np.sqrt(pi) * 0.5 / np.sqrt(nuij) * sp.special.erfc(np.sqrt(nuij) * gamma) * np.exp(nuij * gamma**2)
        I1 = 0.5 / nuij
        Vij = -gsq * Nfac[i] * Nfac[j] * (I1 - gamma * I0)

        Hij[i, j] = Tij + Vij
        Hij[j, i] = Hij[i, j]

# Tips 2 for exercise
- 運動量空間の波動関数を以下の表式で計算しよう[資料の式(A.21)]
    - $ \tilde{u}_0(k) = \sum_i (2\nu_i)^{-3/2} c_i^{(0)} N_i^{(0)} k e^{-\frac{k^2}{4\nu_i}}$
- 直下のセルで一般化固有値方程式を解いている。その結果を利用しよう
    - `wfmom`: 運動量空間の波動関数を代入するためのNumPy配列
    - `nu[i]`: $\nu_i$
    - `Nfac[i]`: $N_i^{(0)}$
    - `evec[i, 0]`: $c_i^{(0)}$. ただし、第2引数`0`は0番目の固有状態を表す
    - 運動量のループに関する変数は上から2番目のコードセルで定義されている
        - `kmx`: 運動量の上限
        - `dk`: 運動量メッシュの刻み
    - 既に`wfmom`が描画されるようになっている

In [ ]:
#--------------------------------
# Generalized eigenvalue problem
#--------------------------------
## Diagonalization
eval, evec = eigh(Hij, Nij)
print("Ground-state energy\n", eval[0], "(MeV)")

## Check for generalized eigenvalue problem
def eig_check(A, B, eigval, eigvec):
    return np.linalg.norm(A.dot(eigvec) - eigval * B.dot(eigvec))

def eig_checks(A, B, eigval, eigvec):
    r = np.zeros(eigval.shape[0])
    i = 0
    for e, v in zip(eigval, eigvec.T):
        r[i] = eig_check(A, B, e, v)
        i += 1
    return r

print("\nCheck for generalized eigenvalue problem\n", eig_checks(Hij, Nij, eval, evec))

## Normalization
sum = 0.0
for i in range(nbmx):
    for j in range(nbmx):
        sum += evec[i, 0] * evec[j, 0] * Nij[i, j]
print("\nNorm\n", sum)

## Wave function in coordinate space
wf = np.zeros(irmx)
for ir in range(irmx):
    r = ir * dr

    for i in range(nbmx):
        phi = Nfac[i] * r * np.exp(-nu[i] * r**2)
        wf[ir] += evec[i, 0] * phi
    
## Wave function in momentum space
wfmom = np.zeros((ikmx, 2))

print()
r_set = np.linspace(0, rmx, irmx)
k_set = np.linspace(0, kmx, ikmx)
plt.figure(figsize=(16, 4.5))
plt.subplot(1, 2, 1)
plt.xlim([0.0, 20.0])
plt.ylim([0.0, 0.6])
plt.plot(r_set, abs(wf))
plt.xlabel("$r$ (fm)")
plt.ylabel("$u_{l}(r)$ (fm$^{-1/2}$)")
plt.tick_params(axis='both', direction='in')
plt.title("Wave function in coordinate space")
plt.subplots_adjust(wspace=0.3)

plt.subplot(1, 2, 2)
plt.xlim([0.0, kmx])
plt.ylim([0.0, 1.6])
plt.plot(k_set, abs(wfmom))
plt.xlabel("$k$ (fm$^{-1}$)")
plt.ylabel("$\\tilde u_{l}(k)$ (fm$^{1/2}$)")
plt.tick_params(axis='both', direction='in')
plt.title("Wave function in momentum space")

plt.show()

# History
## Ver. 00a00 (9/July/2024)
1. First version released.

## Ver. 00a01 (9/July/2024)
1. A bug related to the preparation of the Gaussian range parameters was fixed.

## Ver. 00a02 (15/July/2024)
1. Computation of the matrix elements is now more efficient owing to their symmetry.

## Ver. 00a03 (26/December/2024)
1. Computation of the norm was modified.

## Ver. 00a04 (24/February/2025)
1. The wave function in momentum space was computed.